<a href="https://colab.research.google.com/github/mahamodul05/Extremism/blob/Safwan/EDA.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
# package installation
!pip install pyicu
!pip install pycld2
!pip install polyglot
!pip install textstat
!pip install googletrans

In [1]:
# imports
import warnings
warnings.filterwarnings("ignore")

import os
import gc
import re
import folium
import textstat
from scipy import stats
#import colorama
#from colorama import Fore, Back, Style, init

import math
import numpy as np
import scipy as sp
import pandas as pd

import random
import networkx as nx
from pandas import Timestamp

from PIL import Image
from IPython.display import SVG
from keras.utils import model_to_dot

import requests
from IPython.display import HTML

import seaborn as sns
from tqdm import tqdm
import matplotlib.cm as cm
import matplotlib.pyplot as plt

tqdm.pandas()

import plotly.express as px
import plotly.graph_objects as go
import plotly.figure_factory as ff
from plotly.subplots import make_subplots

import transformers
import tensorflow as tf

from tensorflow.keras.callbacks import Callback
from sklearn.metrics import accuracy_score, roc_auc_score
from tensorflow.keras.callbacks import ModelCheckpoint, ReduceLROnPlateau, CSVLogger

from tensorflow.keras.models import Model
#from kaggle_datasets import KaggleDatasets
from tensorflow.keras.optimizers import Adam
from tokenizers import BertWordPieceTokenizer
from tensorflow.keras.layers import Dense, Input, Dropout, Embedding
from tensorflow.keras.layers import LSTM, GRU, Conv1D, SpatialDropout1D

from tensorflow.keras import layers
from tensorflow.keras import optimizers
from tensorflow.keras import activations
from tensorflow.keras import constraints
from tensorflow.keras import initializers
from tensorflow.keras import regularizers

import tensorflow.keras.backend as K
from tensorflow.keras.layers import *
from tensorflow.keras.optimizers import *
from tensorflow.keras.activations import *
from tensorflow.keras.constraints import *
from tensorflow.keras.initializers import *
from tensorflow.keras.regularizers import *

from sklearn import metrics
from sklearn.utils import shuffle
from gensim.models import Word2Vec
from sklearn.cluster import KMeans
from sklearn.decomposition import PCA
from sklearn.feature_extraction.text import TfidfVectorizer,\
                                            CountVectorizer,\
                                            HashingVectorizer

from nltk.stem.wordnet import WordNetLemmatizer
from nltk.tokenize import word_tokenize
from nltk.tokenize import TweetTokenizer

import nltk
from textblob import TextBlob

from nltk.corpus import wordnet
from nltk.corpus import stopwords
from googletrans import Translator
from nltk import WordNetLemmatizer
from polyglot.detect import Detector
from nltk.stem import WordNetLemmatizer
from wordcloud import WordCloud, STOPWORDS
from nltk.sentiment.vader import SentimentIntensityAnalyzer

stopword=set(STOPWORDS)

lem = WordNetLemmatizer()
tokenizer=TweetTokenizer()

np.random.seed(0)

In [2]:
#val_data = pd.read_csv('validation.csv')
test_data = pd.read_csv('test.csv')
train_data = pd.read_csv('train.csv')

In [3]:
print("Sample train data", train_data.head())
#print("Sample val data", val_data.head())
print("Sample test data", test_data.head())

Sample train data                  id                                       comment_text  toxic  \
0  0000997932d777bf  Explanation\nWhy the edits made under my usern...      0   
1  000103f0d9cfb60f  D'aww! He matches this background colour I'm s...      0   
2  000113f07ec002fd  Hey man, I'm really not trying to edit war. It...      0   
3  0001b41b1c6bb37e  "\nMore\nI can't make any real suggestions on ...      0   
4  0001d958c54c6e35  You, sir, are my hero. Any chance you remember...      0   

   severe_toxic  obscene  threat  insult  identity_hate  
0             0        0       0       0              0  
1             0        0       0       0              0  
2             0        0       0       0              0  
3             0        0       0       0              0  
4             0        0       0       0              0  
Sample test data                  id                                       comment_text
0  00001cee341fdb12  Yo bitch Ja Rule is more succesful the

In [4]:
print(len(train_data))
print(len(test_data))
#print(len(val_data))

159571
114760


In [5]:
# wordcloud for all comments
def nonan(x):
    if type(x) == str:
        return x.replace("\n", "")
    else:
        return ""

text = ' '.join([nonan(abstract) for abstract in train_data["comment_text"]])
wordcloud = WordCloud(max_font_size=None, background_color='black', collocations=False,
                      width=1200, height=1000).generate(text)
fig = px.imshow(wordcloud)
fig.update_layout(title_text='Common words in comments')

In [6]:
def get_language(text):
    return Detector("".join(x for x in text if x.isprintable()), quiet=True).languages[0].name

train_data["lang"] = train_data["comment_text"].progress_apply(get_language)

100%|██████████| 159571/159571 [00:37<00:00, 4220.70it/s]


In [8]:
train_data.head()

id                                       comment_text  toxic  \
0  0000997932d777bf  Explanation\nWhy the edits made under my usern...      0   
1  000103f0d9cfb60f  D'aww! He matches this background colour I'm s...      0   
2  000113f07ec002fd  Hey man, I'm really not trying to edit war. It...      0   
3  0001b41b1c6bb37e  "\nMore\nI can't make any real suggestions on ...      0   
4  0001d958c54c6e35  You, sir, are my hero. Any chance you remember...      0   

   severe_toxic  obscene  threat  insult  identity_hate     lang  
0             0        0       0       0              0  English  
1             0        0       0       0              0  English  
2             0        0       0       0              0  English  
3             0        0       0       0              0  English  
4             0        0       0       0              0  English

In [9]:
# English vs non-English
lang_list = sorted(list(set(train_data["lang"])))
counts = [list(train_data["lang"]).count(cont) for cont in lang_list]
df = pd.DataFrame(np.transpose([lang_list, counts]))
df.columns = ["Language", "Count"]
df["Count"] = df["Count"].apply(int)

df_en = pd.DataFrame(np.transpose([["English", "Non-English"], [max(counts), sum(counts) - max(counts)]]))
df_en.columns = ["Language", "Count"]

fig = px.bar(df_en, x="Language", y="Count", title="Language of comments", color="Language", text="Count")
fig.update_layout(template="plotly_white")
fig.data[0].marker.line.color = 'rgb(0, 0, 0)'
fig.data[0].marker.line.width = 0.5
fig.data[1].marker.line.color = 'rgb(0, 0, 0)'
fig.data[1].marker.line.width = 0.5
fig.data[0].textfont.color = "black"
fig.data[0].textposition = "outside"
fig.data[1].textfont.color = "black"
fig.data[1].textposition = "outside"
fig

In [10]:
df.head()

Language  Count
0         Afar      2
1     Albanian      3
2  Azerbaijani      1
3       Basque      2
4       Breton      5

In [11]:
# Bar chart of non-English languages
fig = px.bar(df.query("Language != 'English' and Language != 'un'").query("Count >= 50"),
             y="Language", x="Count", title="Language of non-English comments", template="plotly_white", color="Language", text="Count", orientation="h")
fig.update_traces(marker=dict(line=dict(width=0.75, color='black')),  textposition="outside")
fig.update_layout(showlegend=False)
fig

In [12]:
# Pie chart of non-English languages
fig = go.Figure([go.Pie(labels=df.query("Language != 'English' and Language != 'un'").query("Count >= 50")["Language"],
           values=df.query("Language != 'English' and Language != 'un'").query("Count >= 50")["Count"])])
fig.update_layout(title_text="Pie chart of non-English languages", template="plotly_white")
fig.data[0].marker.colors = [px.colors.qualitative.Plotly[2:]]
fig.data[0].textfont.color = "black"
fig.data[0].textposition = "outside"
fig.show()

In [14]:
def get_country(language):
    if language == "German":
        return "Germany"
    if language == "Scots":
        return "Scotland"
    if language == "Danish":
        return "Denmark"
    if language == "Arabic":
        return "Saudi Arabia"
    if language == "Spanish":
        return "Spain"
    if language == "Persian":
        return "Iran"
    if language == "Greek":
        return "Greece"
    if language == "Portuguese":
        return "Portugal"
    if language == "English":
        return "United Kingdom"
    if language == "Hindi":
        return "India"
    if language == "Albanian":
        return "Albania"
    if language == "Bosnian":
        return "Bosnia and Herzegovina"
    if language == "Croatian":
        return "Croatia"
    if language == "Dutch":
        return "Netherlands"
    if language == "Russian":
        return "Russia"
    if language == "Vietnamese":
        return "Vietnam"
    if language == "Somali":
        return "Somalia"
    if language == "Turkish":
        return "Turkey"
    if language == "Serbian":
        return "Serbia"
    if language == "Indonesian":
        return "Indonesia"
    if language == "Manx":
        return "Ireland"
    if language == "Scots":
        return "Scotland"
    if language == "Latin":
        return "Holy See (Vatican City State)"
    if language == "Afrikaans":
        return "South Africa"
    return "None"

df["country"] = df["Language"].progress_apply(get_country)
df.head()

100%|██████████| 98/98 [00:00<00:00, 47634.93it/s]


Language  Count  country
0         Afar      2     None
1     Albanian      3  Albania
2  Azerbaijani      1     None
3       Basque      2     None
4       Breton      5     None

In [15]:
# World plot of non-English languages
fig = px.choropleth(df.query("Language != 'English' and Language != 'un' and country != 'None'").query("Count >= 5"), locations="country", hover_name="country",
                     projection="natural earth", locationmode="country names", title="Countries of non-English languages", color="Count",
                     template="plotly", color_continuous_scale="agsunset")
fig.show()

In [16]:
# Non-English European countries
fig = px.choropleth(df.query("Language != 'English' and Language != 'un' and country != 'None'"), locations="country", hover_name="country",
                     projection="natural earth", locationmode="country names", title="Non-English European countries", color="Count",
                     template="plotly", color_continuous_scale="aggrnyl", scope="europe")
fig.show()

In [17]:
# Asian countries
fig = px.choropleth(df.query("Language != 'English' and Language != 'un' and country != 'None'"), locations="country", hover_name="country",
                     projection="natural earth", locationmode="country names", title="Asian countries", color="Count",
                     template="plotly", color_continuous_scale="spectral", scope="asia")
fig.show()

In [18]:
# African countries
fig = px.choropleth(df.query("Language != 'English' and Language != 'un' and country != 'None'").query("Count >= 5"), locations="country", hover_name="country",
                     projection="natural earth", locationmode="country names", title="African countries", color="Count",
                     template="plotly", color_continuous_scale="agsunset", scope="africa")
fig.show()

In [20]:
# Distribution of comment words
def new_len(x):
    if type(x) is str:
        return len(x.split())
    else:
        return 0

train_data["comment_words"] = train_data["comment_text"].apply(new_len)
nums = train_data.query("comment_words != 0 and comment_words < 200").sample(frac=0.1)["comment_words"]
fig = ff.create_distplot(hist_data=[nums],
                         group_labels=["All comments"],
                         colors=["coral"])

fig.update_layout(title_text="Comment words", xaxis_title="Comment words", template="simple_white", showlegend=False)
fig.show()

In [21]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go

# Assuming 'train_data' is your DataFrame and 'lang_list' is a list of languages

# Step 1: Clean the 'comment_words' column
# Convert non-numeric values to NaN
train_data['comment_words'] = pd.to_numeric(train_data['comment_words'], errors='coerce')

# Drop rows with NaN values in 'comment_words'
train_data = train_data.dropna(subset=['comment_words'])

# Step 2: Calculate the mean number of words per comment for each language
mean_comment_words = train_data.groupby("lang")["comment_words"].mean()

# Create the DataFrame with the languages and their average comment words
df = pd.DataFrame({
    "Language": mean_comment_words.index,
    "Average_comment_words": mean_comment_words.values
})

# Step 3: Filter the DataFrame to remove outliers
df = df[df["Average_comment_words"] < 500]

# Step 4: Create the bar chart
fig = go.Figure(go.Bar(x=df["Language"], y=df["Average_comment_words"]))

# Update the layout of the plot
fig.update_layout(
    xaxis_title="Language",
    yaxis_title="Average comment words",
    title_text="Average comment words vs. language",
    template="plotly_white"
)

# Display the plot
fig.show()


In [22]:
import pandas as pd
import numpy as np
import plotly.express as px


train_data['comment_words'] = pd.to_numeric(train_data['comment_words'], errors='coerce')

train_data = train_data.dropna(subset=['comment_words'])

mean_comment_words = train_data.groupby("lang")["comment_words"].mean().reset_index()
mean_comment_words.columns = ["Language", "Average_comment_words"]

def get_country(language):

    language_to_country = {
        # Example mapping
        "English": "United States",
        "Spanish": "Spain",
        # Add more mappings as required
    }
    return language_to_country.get(language, 'None')

mean_comment_words["country"] = mean_comment_words["Language"].apply(get_country)

df = mean_comment_words.query("country != 'None'")

fig = px.choropleth(
    df,
    locations="country",
    hover_name="country",
    projection="natural earth",
    locationmode="country names",
    title="Average comment length vs. Country",
    color="Average_comment_words",
    template="plotly",
    color_continuous_scale="aggrnyl"
)

fig.show()

In [23]:
import nltk
nltk.download('vader_lexicon')

[nltk_data] Downloading package vader_lexicon to /root/nltk_data...
[nltk_data]   Package vader_lexicon is already up-to-date!


True

In [24]:
from nltk.sentiment.vader import SentimentIntensityAnalyzer
SIA = SentimentIntensityAnalyzer()

In [25]:
def polarity(x):
    if type(x) == str:
        return SIA.polarity_scores(x)
    else:
        return 1000

SIA = SentimentIntensityAnalyzer()
train_data["polarity"] = train_data["comment_text"].progress_apply(polarity)

100%|██████████| 159571/159571 [02:33<00:00, 1036.36it/s]


In [26]:
# Negative sentiment
fig = go.Figure(go.Histogram(x=[pols["neg"] for pols in train_data["polarity"] if pols["neg"] != 0], marker=dict(
            color='seagreen')
    ))

fig.update_layout(xaxis_title="Negativity sentiment", title_text="Negativity sentiment", template="simple_white")
fig.show()

In [27]:
# Calculate Negativity
train_data["negativity"] = train_data["polarity"].apply(lambda x: x["neg"])

# Group Data by Language and Calculate Mean Negativity
mean_negativity_by_language = train_data.groupby("lang")["negativity"].mean()

# Create DataFrame
df = pd.DataFrame({
    "Language": mean_negativity_by_language.index,
    "Negativity": mean_negativity_by_language.values
})

# Convert Negativity to float
df["Negativity"] = df["Negativity"].astype(float)

# Filter Data
df = df.query("Negativity != 0")
df["country"] = df["Language"].apply(get_country)
df = df.query("country != 'None'")

# Create Choropleth Map
fig = px.choropleth(
    df,
    locations="country",
    hover_name="country",
    projection="natural earth",
    locationmode="country names",
    title="Average Negative Sentiment vs. Country",
    color="Negativity",
    template="plotly",
    color_continuous_scale="greens"
)

# Show the plot
fig.show()

In [28]:
# Negativity vs. Toxicity

nums_1 = train_data.sample(frac=0.1).query("toxic == 1")["negativity"]
nums_2 = train_data.sample(frac=0.1).query("toxic == 0")["negativity"]

fig = ff.create_distplot(hist_data=[nums_1, nums_2],
                         group_labels=["Toxic", "Non-toxic"],
                         colors=["darkorange", "dodgerblue"], show_hist=False)

fig.update_layout(title_text="Negativity vs. Toxicity", xaxis_title="Negativity", template="simple_white")
fig.show()

In [29]:
# Positive sentiment
fig = go.Figure(go.Histogram(x=[pols["pos"] for pols in train_data["polarity"] if pols["pos"] != 0], marker=dict(
            color='indianred')
    ))

fig.update_layout(xaxis_title="Positivity sentiment", title_text="Positivity sentiment", template="simple_white")
fig.show()

In [30]:
# Calculate Positivity
train_data["positivity"] = train_data["polarity"].apply(lambda x: x["pos"])

# Group Data by Language and Calculate Mean Positivity
mean_positivity_by_language = train_data.groupby("lang")["positivity"].mean()

# Create DataFrame
df = pd.DataFrame({
    "Language": mean_positivity_by_language.index,
    "Positivity": mean_positivity_by_language.values
})

# Convert Positivity to float
df["Positivity"] = df["Positivity"].astype(float)

# Map Languages to Countries
df["country"] = df["Language"].apply(get_country)
df = df.query("country != 'None'")

# Create Choropleth Map
fig = px.choropleth(
    df,
    locations="country",
    hover_name="country",
    projection="natural earth",
    locationmode="country names",
    title="Average Positive Sentiment vs. Country",
    color="Positivity",
    template="plotly",
    color_continuous_scale="reds"
)

# Show the plot
fig.show()


In [31]:
# Positivity vs. Toxicity

nums_1 = train_data.sample(frac=0.1).query("toxic == 1")["positivity"]
nums_2 = train_data.sample(frac=0.1).query("toxic == 0")["positivity"]

fig = ff.create_distplot(hist_data=[nums_1, nums_2],
                         group_labels=["Toxic", "Non-toxic"],
                         colors=["darkorange", "dodgerblue"], show_hist=False)

fig.update_layout(title_text="Positivity vs. Toxicity", xaxis_title="Positivity", template="simple_white")
fig.show()

In [32]:
# Neutrality sentiment
fig = go.Figure(go.Histogram(x=[pols["neu"] for pols in train_data["polarity"] if pols["neu"] != 1], marker=dict(
            color='dodgerblue')
    ))

fig.update_layout(xaxis_title="Neutrality sentiment", title_text="Neutrality sentiment", template="simple_white")
fig.show()

In [33]:
# Calculate Neutrality
train_data["neutrality"] = train_data["polarity"].apply(lambda x: x["neu"])

# Group Data by Language and Calculate Mean Neutrality
mean_neutrality_by_language = train_data.groupby("lang")["neutrality"].mean()

# Create DataFrame
df = pd.DataFrame({
    "Language": mean_neutrality_by_language.index,
    "Neutrality": mean_neutrality_by_language.values
})

# Convert Neutrality to float
df["Neutrality"] = df["Neutrality"].astype(float)

# Filter Data
df = df.query("Neutrality != 1")
df["country"] = df["Language"].apply(get_country)
df = df.query("country != 'None'")

# Create Choropleth Map
fig = px.choropleth(
    df,
    locations="country",
    hover_name="country",
    projection="natural earth",
    locationmode="country names",
    title="Average Neutral Sentiment vs. Country",
    color="Neutrality",
    template="plotly",
    color_continuous_scale="blues"
)

# Show the plot
fig.show()

In [34]:
# Neutrality vs. Toxicity
nums_1 = train_data.sample(frac=0.1).query("toxic == 1")["neutrality"]
nums_2 = train_data.sample(frac=0.1).query("toxic == 0")["neutrality"]

fig = ff.create_distplot(hist_data=[nums_1, nums_2],
                         group_labels=["Toxic", "Non-toxic"],
                         colors=["darkorange", "dodgerblue"], show_hist=False)

fig.update_layout(title_text="Neutrality vs. Toxicity", xaxis_title="Neutrality", template="simple_white")
fig.show()

In [35]:
# Compound sentiment
fig = go.Figure(go.Histogram(x=[pols["compound"] for pols in train_data["polarity"] if pols["compound"] != 0], marker=dict(
            color='orchid')
    ))

fig.update_layout(xaxis_title="Compound sentiment", title_text="Compound sentiment", template="simple_white")
fig.show()

In [37]:
# Calculate Compound Sentiment
train_data["compound"] = train_data["polarity"].apply(lambda x: x["compound"])

# Group Data by Language and Calculate Mean Compound Sentiment
mean_compound_by_language = train_data.groupby("lang")["compound"].mean()

# Create DataFrame
df = pd.DataFrame({
    "Language": mean_compound_by_language.index,
    "Compound": mean_compound_by_language.values
})

# Convert Compound Sentiment to float
df["Compound"] = df["Compound"].astype(float)

# Filter Data
df = df.query("Compound != 0")
df["country"] = df["Language"].apply(get_country)
df = df.query("country != 'None'")

# Create Choropleth Map
fig = px.choropleth(
    df,
    locations="country",
    hover_name="country",
    projection="natural earth",
    locationmode="country names",
    title="Average Compound Sentiment vs. Country",
    color="Compound",
    template="plotly",
    color_continuous_scale="purples"
)

# Show the plot
fig.show()

In [38]:
# Compound sentiment vs. Toxicity

nums_1 = train_data.sample(frac=0.1).query("toxic == 1")["compound"]
nums_2 = train_data.sample(frac=0.1).query("toxic == 0")["compound"]

fig = ff.create_distplot(hist_data=[nums_1, nums_2],
                         group_labels=["Toxic", "Non-toxic"],
                         colors=["darkorange", "dodgerblue"], show_hist=False)

fig.update_layout(title_text="Compound vs. Toxicity", xaxis_title="Compound", template="simple_white")
fig.show()

In [39]:
train_data["flesch_reading_ease"] = train_data["comment_text"].progress_apply(textstat.flesch_reading_ease)
train_data["automated_readability"] = train_data["comment_text"].progress_apply(textstat.automated_readability_index)
train_data["dale_chall_readability"] = train_data["comment_text"].progress_apply(textstat.dale_chall_readability_score)
#The Flesch Reading Ease score is a measure of how easy it is to understand a piece of text. Higher scores indicate easier readability.
#The Automated Readability Index (ARI) is a formula that computes the approximate reading level of a piece of text based on its average number of words per sentence and average number of syllables per word.
#The Dale-Chall Readability Score is another readability metric that considers the complexity of words used in a text. It is based on a list of familiar words.

100%|██████████| 159571/159571 [01:02<00:00, 2564.07it/s]


In [40]:
# Distribution of Flesch reading ease

fig = go.Figure(go.Histogram(x=train_data.query("flesch_reading_ease > 0")["flesch_reading_ease"], marker=dict(
            color='darkorange')
    ))

fig.update_layout(xaxis_title="Flesch reading ease", title_text="Flesch reading ease", template="simple_white")
fig.show()

In [42]:
# Group Data by Language and Calculate Mean Flesch Reading Ease
mean_flesch_by_language = train_data.groupby("lang")["flesch_reading_ease"].mean()

# Create DataFrame
df = pd.DataFrame({
    "Language": mean_flesch_by_language.index,
    "flesch_reading_ease": mean_flesch_by_language.values
})

# Convert Flesch Reading Ease to float
df["flesch_reading_ease"] = df["flesch_reading_ease"].astype(float)

# Filter Data
df = df.query("flesch_reading_ease > 0")
df["country"] = df["Language"].apply(get_country)
df = df.query("country != 'None'")

# Create Choropleth Map
fig = px.choropleth(
    df,
    locations="country",
    hover_name="country",
    projection="natural earth",
    locationmode="country names",
    title="Average Flesch Reading Ease vs. Country",
    color="flesch_reading_ease",
    template="plotly",
    color_continuous_scale="oranges"
)

# Show the plot
fig.show()

In [43]:
# Flesch reading ease vs. Toxicity

nums_1 = train_data.sample(frac=0.1).query("toxic == 1")["flesch_reading_ease"]
nums_2 = train_data.sample(frac=0.1).query("toxic == 0")["flesch_reading_ease"]

fig = ff.create_distplot(hist_data=[nums_1, nums_2],
                         group_labels=["Toxic", "Non-toxic"],
                         colors=["darkorange", "dodgerblue"], show_hist=False)

fig.update_layout(title_text="Flesch reading ease vs. Toxicity", xaxis_title="Flesch reading ease", template="simple_white")
fig.show()

In [44]:
# Distribution of automated readability

fig = go.Figure(go.Histogram(x=train_data.query("automated_readability < 100")["automated_readability"], marker=dict(
            color='mediumaquamarine')
    ))

fig.update_layout(xaxis_title="Automated readability", title_text="Automated readability", template="simple_white")
fig.show()

In [46]:
# Group Data by Language and Calculate Mean Automated Readability
mean_automated_readability_by_language = train_data.groupby("lang")["automated_readability"].mean()

# Create DataFrame
df = pd.DataFrame({
    "Language": mean_automated_readability_by_language.index,
    "automated_readability": mean_automated_readability_by_language.values
})

# Convert Automated Readability to float
df["automated_readability"] = df["automated_readability"].astype(float)

# Filter Data
df = df.query("automated_readability < 100")
df["country"] = df["Language"].apply(get_country)
df = df.query("country != 'None'")

# Create Choropleth Map
fig = px.choropleth(
    df,
    locations="country",
    hover_name="country",
    projection="natural earth",
    locationmode="country names",
    title="Automated Readability vs. Country",
    color="automated_readability",
    template="plotly",
    color_continuous_scale="GnBu"
)

# Show the plot
fig.show()

In [47]:
# Automated readability vs. Toxicity

nums_1 = train_data.sample(frac=0.1).query("toxic == 1")["automated_readability"]
nums_2 = train_data.sample(frac=0.1).query("toxic == 0")["automated_readability"]

fig = ff.create_distplot(hist_data=[nums_1, nums_2],
                         group_labels=["Toxic", "Non-toxic"],
                         colors=["darkorange", "dodgerblue"], show_hist=False)

fig.update_layout(title_text="Automated readability vs. Toxicity", xaxis_title="Automated readability", template="simple_white")
fig.show()

In [48]:
# Distribution of Dale-Chall readability

fig = go.Figure(go.Histogram(x=train_data.query("dale_chall_readability < 20")["dale_chall_readability"], marker=dict(
            color='deeppink')
    ))

fig.update_layout(xaxis_title="Dale-Chall readability", title_text="Dale-Chall readability", template="simple_white")
fig.show()

In [49]:
# Group Data by Language and Calculate Mean Dale-Chall Readability
mean_dale_chall_readability_by_language = train_data.groupby("lang")["dale_chall_readability"].mean()

# Create DataFrame
df = pd.DataFrame({
    "Language": mean_dale_chall_readability_by_language.index,
    "dale_chall_readability": mean_dale_chall_readability_by_language.values
})

# Convert Dale-Chall Readability to float
df["dale_chall_readability"] = df["dale_chall_readability"].astype(float)

# Filter Data
df = df.query("dale_chall_readability < 20")
df["country"] = df["Language"].apply(get_country)
df = df.query("country != 'None'")

# Create Choropleth Map
fig = px.choropleth(
    df,
    locations="country",
    hover_name="country",
    projection="natural earth",
    locationmode="country names",
    title="Dale-Chall Readability vs. Country",
    color="dale_chall_readability",
    template="plotly",
    color_continuous_scale="PuRd"
)

# Show the plot
fig.show()

In [50]:
# Dale-Chall readability

nums_1 = train_data.sample(frac=0.1).query("toxic == 1")["dale_chall_readability"]
nums_2 = train_data.sample(frac=0.1).query("toxic == 0")["dale_chall_readability"]

fig = ff.create_distplot(hist_data=[nums_1, nums_2],
                         group_labels=["Toxic", "Non-toxic"],
                         colors=["darkorange", "dodgerblue"], show_hist=False)

fig.update_layout(title_text="Dale-Chall readability vs. Toxicity", xaxis_title="Dale-Chall readability", template="simple_white")
fig.show()

In [52]:
# Pie chart of targets

fig = go.Figure(data=[
    go.Pie(labels=train_data.columns[2:7],
           values=train_data.iloc[:, 2:7].sum().values, marker=dict(colors=px.colors.qualitative.Plotly))
])
fig.update_traces(textposition='outside', textfont=dict(color="black"))
fig.update_layout(title_text="Pie chart of labels")
fig.show()

In [53]:
# Bar chart of targets

fig = go.Figure(data=[
    go.Bar(y=train_data.columns[2:7],
           x=train_data.iloc[:, 2:7].sum().values, marker=dict(color=px.colors.qualitative.Plotly))
])

fig.data[0].marker.line.color = 'rgb(0, 0, 0)'
fig.data[0].marker.line.width = 0.75
fig.update_traces(orientation="h")
fig.update_layout(title_text="Bar chart of labels", template="plotly_white")
fig.show()

In [55]:
# Group Data by Language and Calculate Mean Toxicity
mean_toxicity_by_language = train_data.groupby("lang")["toxic"].mean()

# Create DataFrame
df = pd.DataFrame({
    "Language": mean_toxicity_by_language.index,
    "toxicity": mean_toxicity_by_language.values
})

# Convert Toxicity to float
df["toxicity"] = df["toxicity"].astype(float)

# Map Languages to Countries
df["country"] = df["Language"].apply(get_country)
df = df.query("country != 'None'")

# Create Choropleth Map
fig = px.choropleth(
    df,
    locations="country",
    hover_name="country",
    projection="natural earth",
    locationmode="country names",
    title="Average Toxicity vs. Country",
    color="toxicity",
    template="plotly",
    color_continuous_scale="tealrose"
)

# Show the plot
fig.show()


In [ ]:
# Non-toxic vs. Toxic

clean_mask=np.array(Image.open("../input/imagesforkernal/safe-zone.png"))
clean_mask=clean_mask[:,:,1]

subset = train_data.query("toxic == 0")
text = subset.comment_text.values
wc = WordCloud(background_color="black",max_words=2000,mask=clean_mask,stopwords=stopword)
wc.generate(" ".join(text))
plt.figure(figsize=(7.5, 7.5))
plt.axis("off")
plt.title("Words frequented in Clean Comments", fontsize=16)
plt.imshow(wc.recolor(colormap= 'viridis' , random_state=17), alpha=0.98)
plt.show()

clean_mask=np.array(Image.open("../input/imagesforkernal/swords.png"))
clean_mask=clean_mask[:,:,1]

subset = train_data.query("toxic == 1")
text = subset.comment_text.values
wc = WordCloud(background_color="black",max_words=2000,mask=clean_mask,stopwords=stopword)
wc.generate(" ".join(text))
plt.figure(figsize=(7.5, 7.5))
plt.axis("off")
plt.title("Words frequented in Toxic Comments", fontsize=16)
plt.imshow(wc.recolor(colormap= 'viridis' , random_state=17), alpha=0.98)
plt.show()

In [ ]:
# Obscene vs. Severe Toxic vs. Threat vs. Insult

toxic_mask=np.array(Image.open("../input/imagesforkernal/toxic-sign.png"))
toxic_mask=toxic_mask[:,:,1]
#wordcloud for clean comments
subset=train_data.query("obscene == 1")
text=subset.comment_text.values
wc= WordCloud(background_color="black",max_words=4000,mask=toxic_mask,stopwords=stopword)
wc.generate(" ".join(text))
plt.figure(figsize=(20,20))
plt.subplot(221)
plt.axis("off")
plt.title("Words frequented in Obscene Comments", fontsize=20)
plt.imshow(wc.recolor(colormap= 'gist_earth' , random_state=244), alpha=0.98)

#Severely toxic comments
plt.subplot(222)
severe_toxic_mask=np.array(Image.open("../input/imagesforkernal/bomb.png"))
severe_toxic_mask=severe_toxic_mask[:,:,1]
subset=train_data[train_data.severe_toxic==1]
text=subset.comment_text.values
wc= WordCloud(background_color="black",max_words=2000,mask=severe_toxic_mask,stopwords=stopword)
wc.generate(" ".join(text))
plt.axis("off")
plt.title("Words frequented in Severe Toxic Comments", fontsize=20)
plt.imshow(wc.recolor(colormap= 'Reds' , random_state=244), alpha=0.98)

#Threat comments
plt.subplot(223)
threat_mask=np.array(Image.open("../input/imagesforkernal/anger.png"))
threat_mask=threat_mask[:,:,1]
subset=train_data[train_data.threat==1]
text=subset.comment_text.values
wc= WordCloud(background_color="black",max_words=2000,mask=threat_mask,stopwords=stopword)
wc.generate(" ".join(text))
plt.axis("off")
plt.title("Words frequented in Threatening Comments", fontsize=20)
plt.imshow(wc.recolor(colormap= 'summer' , random_state=2534), alpha=0.98)

#insult
plt.subplot(224)
insult_mask=np.array(Image.open("../input/imagesforkernal/swords.png"))
insult_mask=insult_mask[:,:,1]
subset=train_data[train_data.insult==1]
text=subset.comment_text.values
wc= WordCloud(background_color="black",max_words=2000,mask=insult_mask,stopwords=stopword)
wc.generate(" ".join(text))
plt.axis("off")
plt.title("Words frequented in insult Comments", fontsize=20)
plt.imshow(wc.recolor(colormap= 'Paired_r' , random_state=244), alpha=0.98)

plt.show()